In [65]:
import matplotlib.pyplot as plt
import numpy as np
import matplotlib.image as mpimg
import csv
import cv2

In [66]:
def get_answer_list(file_name, screen_num):
    axis_list = list()
    with open(file_name, 'r') as csv_file:
        reader = csv.DictReader(csv_file, delimiter='\t')
        for row in reader:
            if int(row['screen_num']) == screen_num:
                coordinate = [int(row['x1']), int(row['y1']),\
                              int(row['x2']), int(row['y2'])]
                axis_list.append(coordinate)
    return axis_list

In [67]:
#이미지 비율 조정
def rescale_img(img, scale_percent):
    width = int(img.shape[1] * scale_percent / 100)
    height = int(img.shape[0] * scale_percent / 100)
    dim = (width, height)
    reimg = cv2.resize(img, dim, interpolation = cv2.INTER_AREA)
    return reimg

In [68]:
# 이미지 데이터 읽기
def show_img(img):
    img_resized=rescale_img(img, 30)
    cv2.imshow('mser', img_resized)
    cv2.waitKey(0)
    cv2.destroyAllWindows()

In [69]:
test_img_url = '/home/kimsoohyun/00-Research/02-Graph/02-image_detection/04-clickable/dataset/00-screenshot/kr.co.company.hwahae/3.png'
answer_url = '/home/kimsoohyun/00-Research/02-Graph/02-image_detection/04-clickable/dataset/01-csv/clickable/kr.co.company.hwahae.csv'
answer_list = get_answer_list(answer_url, 3)
img = cv2.imread(test_img_url)
print(len(answer_list))

38


In [70]:
def get_img_gradient_info(img):
    gray = cv2.cvtColor(img, cv2.COLOR_BGR2GRAY)
    X = cv2.Sobel(gray, cv2.CV_32F, 1, 0)
    Y = cv2.Sobel(gray, cv2.CV_32F, 0, 1)

    orien = cv2.phase(X, Y, angleInDegrees=True)
    mag = cv2.magnitude(X, Y)
    return orien, mag

In [71]:
def find_adjacement(p, non_zero_list, WIDTH, HEIGHT):
    adj_set = set()
    ld_y = p[1] - 1
    ld_x = p[0] - 1
    for x_bias in range(3):
        adj_x = ld_x + x_bias
        #print("[DEBUG] adj_x: ",adj_x)
        if adj_x < 0 or adj_x >= WIDTH:
            continue
        for y_bias in range(3):
            adj_y = ld_y + y_bias
            #print("[DEBUG] adj_y: ",adj_y)

            if adj_y < 0 or adj_y >= HEIGHT:
                continue
            adj_p = (adj_x, adj_y) 
            #print("[DEBUG] adjace_pixel: ",adj_p)
            if adj_p in non_zero_list:
                #print("[DEBUG] EXIST!: ",adj_p)
                adj_set.add(adj_p)
    return adj_set
            

In [11]:
def get_edgegroups(img, HEIGHT, WIDTH):
    re_img = rescale_img(img, 30)
    _, mag = get_img_gradient_info(re_img)
    raw_nonzero = np.nonzero(mag)
    non_zero_list = list(zip(raw_nonzero[0], raw_nonzero[1]))
    edge_groups = dict()
    non_zero_set = set(non_zero_list)
    pixel = non_zero_set.pop()
    print("[DEBUG] pixel", pixel)
    while len(non_zero_set) > 0:
        test_group = set()
        edge_group = set()
        test_group.add(pixel)
        while len(test_group) > 0:
            test_pixel = test_group.pop()
            edge_group.add(test_pixel)
            pixel_set = find_adjacement(test_pixel, non_zero_list,\
                                        HEIGHT, WIDTH)
            print("[DEBUG] pixel_set: ", pixel_set)
            pixel_set = pixel_set - edge_group
            test_group = test_group.union(pixel_set)
            print("[DEBUG] test_group: ", len(test_group))
        edge_groups.update({pixel:edge_group})
        non_zero_set = set(non_zero_list)
        non_zero_set = non_zero_set - edge_group
        if len(non_zero_set) > 0:
            pixel = non_zero_set.pop()
    return edge_groups
get_edgegroups(img, 2960,1440)

[DEBUG] pixel (727, 68)
[DEBUG] pixel_set:  {(726, 67), (727, 68), (727, 69), (728, 69), (726, 69), (728, 68), (726, 68), (727, 67), (728, 67)}
[DEBUG] test_group:  8
[DEBUG] pixel_set:  {(726, 67), (727, 68), (726, 66), (725, 66), (727, 66), (725, 67), (726, 68), (725, 68), (727, 67)}
[DEBUG] test_group:  12
[DEBUG] pixel_set:  {(727, 68), (727, 69), (728, 70), (728, 69), (726, 69), (728, 68), (726, 68), (726, 70), (727, 70)}
[DEBUG] test_group:  14
[DEBUG] pixel_set:  {(726, 67), (726, 66), (725, 65), (725, 66), (727, 66), (725, 67), (727, 67), (727, 65), (726, 65)}
[DEBUG] test_group:  16
[DEBUG] pixel_set:  {(727, 69), (728, 71), (728, 70), (729, 69), (728, 69), (729, 70), (729, 71), (727, 70), (727, 71)}
[DEBUG] test_group:  20
[DEBUG] pixel_set:  {(729, 68), (728, 70), (729, 69), (728, 69), (729, 70), (728, 68), (730, 69), (730, 68), (730, 70)}
[DEBUG] test_group:  23
[DEBUG] pixel_set:  {(726, 67), (726, 66), (724, 67), (724, 66), (725, 65), (724, 65), (725, 66), (725, 67), (726

[DEBUG] pixel_set:  {(716, 66), (716, 65), (715, 66), (715, 67), (715, 65), (714, 65), (714, 67), (716, 67), (714, 66)}
[DEBUG] test_group:  131
[DEBUG] pixel_set:  {(716, 66), (717, 65), (716, 65), (717, 66), (716, 64), (715, 66), (715, 64), (715, 65), (717, 64)}
[DEBUG] test_group:  132
[DEBUG] pixel_set:  {(716, 66), (716, 65), (716, 64), (715, 66), (715, 64), (715, 65), (714, 65), (714, 66)}
[DEBUG] test_group:  131
[DEBUG] pixel_set:  {(731, 64), (731, 65), (730, 65), (729, 63), (730, 64), (730, 63), (729, 64), (729, 65), (731, 63)}
[DEBUG] test_group:  131
[DEBUG] pixel_set:  {(718, 63), (720, 63), (718, 62), (720, 62), (719, 62), (720, 61), (719, 63), (719, 61), (718, 61)}
[DEBUG] test_group:  130
[DEBUG] pixel_set:  {(724, 58), (723, 60), (723, 58), (722, 59), (723, 59), (722, 58), (724, 60), (722, 60), (724, 59)}
[DEBUG] test_group:  132
[DEBUG] pixel_set:  {(724, 58), (725, 57), (724, 57), (725, 58), (725, 59), (723, 58), (723, 59), (723, 57), (724, 59)}
[DEBUG] test_group:  

[DEBUG] test_group:  160
[DEBUG] pixel_set:  {(722, 57), (722, 56), (723, 58), (722, 58), (723, 56), (721, 56), (723, 57), (721, 57), (721, 58)}
[DEBUG] test_group:  160
[DEBUG] pixel_set:  {(722, 67), (724, 67), (722, 66), (724, 66), (723, 68), (722, 68), (723, 66), (723, 67), (724, 68)}
[DEBUG] test_group:  159
[DEBUG] pixel_set:  {(727, 66), (729, 64), (727, 64), (728, 66), (729, 65), (727, 65), (728, 65), (728, 64), (729, 66)}
[DEBUG] test_group:  158
[DEBUG] pixel_set:  {(720, 69), (718, 69), (720, 68), (718, 68), (719, 67), (720, 67), (718, 67), (719, 69), (719, 68)}
[DEBUG] test_group:  157
[DEBUG] pixel_set:  {(712, 57), (713, 58), (713, 59), (712, 58), (712, 59), (713, 57)}
[DEBUG] test_group:  157
[DEBUG] pixel_set:  {(728, 62), (727, 62), (729, 62), (727, 63), (729, 63), (729, 64), (727, 64), (728, 64), (728, 63)}
[DEBUG] test_group:  156
[DEBUG] pixel_set:  {(719, 59), (719, 57), (718, 57), (718, 59), (720, 59), (718, 58), (720, 58), (720, 57), (719, 58)}
[DEBUG] test_group

[DEBUG] pixel_set:  {(718, 48), (717, 46), (717, 47), (717, 48), (718, 47), (718, 46), (719, 46), (719, 48), (719, 47)}
[DEBUG] test_group:  181
[DEBUG] pixel_set:  {(719, 45), (717, 45), (717, 46), (717, 47), (718, 45), (718, 47), (718, 46), (719, 46), (719, 47)}
[DEBUG] test_group:  183
[DEBUG] pixel_set:  {(719, 45), (718, 45), (718, 47), (720, 47), (718, 46), (720, 46), (719, 46), (720, 45), (719, 47)}
[DEBUG] test_group:  185
[DEBUG] pixel_set:  {(716, 53), (716, 52), (717, 53), (716, 51), (715, 52), (717, 51), (715, 53), (717, 52), (715, 51)}
[DEBUG] test_group:  184
[DEBUG] pixel_set:  {(720, 49), (718, 49), (720, 48), (718, 48), (718, 47), (720, 47), (719, 48), (719, 47), (719, 49)}
[DEBUG] test_group:  185
[DEBUG] pixel_set:  {(719, 44), (721, 45), (719, 45), (721, 46), (721, 44), (720, 46), (719, 46), (720, 45), (720, 44)}
[DEBUG] test_group:  189
[DEBUG] pixel_set:  {(719, 44), (720, 43), (719, 45), (721, 43), (719, 43), (721, 44), (721, 45), (720, 45), (720, 44)}
[DEBUG] te

[DEBUG] pixel_set:  {(725, 46), (726, 45), (726, 44), (726, 46), (727, 46), (727, 44), (725, 44), (727, 45), (725, 45)}
[DEBUG] test_group:  266
[DEBUG] pixel_set:  {(729, 61), (729, 62), (729, 63), (730, 61), (730, 63), (730, 62), (731, 62), (731, 63), (731, 61)}
[DEBUG] test_group:  265
[DEBUG] pixel_set:  {(727, 72), (725, 72), (727, 73), (725, 73), (726, 73), (726, 71), (726, 72), (725, 71), (727, 71)}
[DEBUG] test_group:  268
[DEBUG] pixel_set:  {(725, 72), (724, 74), (725, 73), (726, 73), (724, 73), (725, 74), (726, 72), (724, 72), (726, 74)}
[DEBUG] test_group:  272
[DEBUG] pixel_set:  {(723, 72), (723, 73), (723, 71), (725, 72), (725, 73), (724, 71), (724, 73), (724, 72), (725, 71)}
[DEBUG] test_group:  273
[DEBUG] pixel_set:  {(728, 73), (728, 72), (727, 74), (727, 72), (727, 73), (726, 73), (726, 72), (726, 74), (728, 74)}
[DEBUG] test_group:  274
[DEBUG] pixel_set:  {(725, 47), (726, 49), (726, 47), (726, 48), (725, 48), (725, 49), (724, 47), (724, 49), (724, 48)}
[DEBUG] te

...

[DEBUG] pixel_set:  {(694, 52), (695, 51), (696, 51), (696, 50), (694, 51), (695, 52), (694, 50), (695, 50), (696, 52)}
[DEBUG] test_group:  503
[DEBUG] pixel_set:  {(700, 63), (700, 62), (700, 61), (698, 61), (698, 63), (698, 62), (699, 62), (699, 63), (699, 61)}
[DEBUG] test_group:  502
[DEBUG] pixel_set:  {(694, 52), (694, 54), (695, 54), (695, 52), (695, 53), (696, 54), (696, 53), (694, 53), (696, 52)}
[DEBUG] test_group:  501
[DEBUG] pixel_set:  {(708, 71), (708, 72), (707, 72), (707, 70), (707, 71)}
[DEBUG] test_group:  501
[DEBUG] pixel_set:  {(701, 40), (701, 41), (700, 42), (702, 41), (700, 41), (701, 42), (702, 40), (700, 40), (702, 42)}
[DEBUG] test_group:  503
[DEBUG] pixel_set:  {(701, 39), (701, 40), (701, 41), (702, 41), (700, 41), (702, 40), (700, 40), (700, 39), (702, 39)}
[DEBUG] test_group:  505
[DEBUG] pixel_set:  {(697, 74), (697, 75), (697, 76), (698, 74), (698, 76), (698, 75), (696, 76), (696, 75), (696, 74)}
[DEBUG] test_group:  504
[DEBUG] pixel_set:  {(706, 92

[DEBUG] pixel_set:  {(693, 40), (692, 39), (692, 38), (692, 40), (693, 38), (693, 39)}
[DEBUG] test_group:  490
[DEBUG] pixel_set:  {(693, 40), (693, 41), (692, 39), (692, 40), (693, 39)}
[DEBUG] test_group:  489
[DEBUG] pixel_set:  {(703, 40), (703, 39), (703, 41), (704, 39), (705, 40), (705, 41), (705, 39), (704, 41), (704, 40)}
[DEBUG] test_group:  490
[DEBUG] pixel_set:  {(703, 40), (703, 39), (703, 41), (702, 41), (702, 40), (704, 39), (704, 41), (704, 40), (702, 39)}
[DEBUG] test_group:  489
[DEBUG] pixel_set:  {(706, 39), (706, 38), (706, 40), (707, 40), (705, 40), (705, 38), (707, 38), (705, 39), (707, 39)}
[DEBUG] test_group:  491
[DEBUG] pixel_set:  {(706, 39), (706, 38), (705, 37), (705, 38), (707, 38), (705, 39), (707, 39), (706, 37), (707, 37)}
[DEBUG] test_group:  493
[DEBUG] pixel_set:  {(706, 38), (708, 38), (708, 37), (707, 38), (706, 37), (707, 37)}
[DEBUG] test_group:  494
[DEBUG] pixel_set:  {(708, 37), (708, 38), (707, 38), (707, 37)}
[DEBUG] test_group:  493
[DEBU

[DEBUG] pixel_set:  {(701, 28), (701, 29), (700, 29), (700, 28), (699, 28), (699, 29)}
[DEBUG] test_group:  535
[DEBUG] pixel_set:  {(701, 28), (701, 29), (700, 29), (700, 28), (702, 29)}
[DEBUG] test_group:  535
[DEBUG] pixel_set:  {(700, 31), (700, 30), (701, 29), (700, 29), (701, 30), (701, 31), (699, 30), (699, 31), (699, 29)}
[DEBUG] test_group:  536
[DEBUG] pixel_set:  {(700, 31), (700, 30), (702, 32), (701, 30), (701, 31), (701, 32), (702, 31), (700, 32), (702, 30)}
[DEBUG] test_group:  540
[DEBUG] pixel_set:  {(702, 33), (702, 32), (701, 31), (701, 32), (701, 33), (702, 31), (703, 32), (703, 31), (703, 33)}
[DEBUG] test_group:  542
[DEBUG] pixel_set:  {(703, 29), (701, 29), (701, 30), (701, 31), (702, 29), (702, 31), (702, 30), (703, 30), (703, 31)}
[DEBUG] test_group:  543
[DEBUG] pixel_set:  {(704, 32), (702, 32), (702, 31), (704, 31), (702, 30), (704, 30), (703, 30), (703, 32), (703, 31)}
[DEBUG] test_group:  545
[DEBUG] pixel_set:  {(700, 31), (702, 33), (702, 32), (701, 31

[DEBUG] pixel_set:  {(704, 88), (702, 87), (703, 88), (703, 87), (702, 88), (704, 87)}
[DEBUG] test_group:  499
[DEBUG] pixel_set:  {(695, 36), (695, 37), (697, 36), (696, 38), (697, 37), (696, 37), (697, 38), (696, 36), (695, 38)}
[DEBUG] test_group:  498
[DEBUG] pixel_set:  {(698, 33), (697, 31), (698, 32), (698, 31), (697, 32), (697, 33), (696, 33), (696, 32), (696, 31)}
[DEBUG] test_group:  497
[DEBUG] pixel_set:  {(694, 148), (694, 147), (694, 146), (692, 146), (693, 146), (693, 147)}
[DEBUG] test_group:  496
[DEBUG] pixel_set:  {(702, 44), (703, 43), (701, 43), (702, 43), (703, 44), (701, 44), (703, 45), (701, 45), (702, 45)}
[DEBUG] test_group:  495
[DEBUG] pixel_set:  {(707, 130), (707, 128), (707, 129), (706, 129), (706, 128), (706, 130)}
[DEBUG] test_group:  494
[DEBUG] pixel_set:  {(703, 38), (703, 36), (703, 37), (704, 38), (705, 37), (704, 37), (705, 38), (704, 36)}
[DEBUG] test_group:  493
[DEBUG] pixel_set:  {(699, 40), (697, 38), (699, 38), (697, 39), (698, 40), (699, 3

KeyboardInterrupt: 

In [72]:
def get_edgegroups_v2(mag, non_zero_list, HEIGHT, WIDTH):
    edge_groups = dict()
    count = 0
    for i in range(WIDTH):
        for j in range(HEIGHT):
            print("[DEBUG] WIDTH:{} HEIGHT:{}".format(i, j))
            if mag[j][i] != 0:
                if len(edge_groups.keys()) == 0:
                    edge_groups.update({count: {(j, i)}})
                    count += 1
                else:
                    key_list = list(edge_groups.keys()).copy()
                    is_contain = False
                    print("[DEBUG] KEY_LIST: ", key_list)
                    for key in key_list:
                        adj_set = find_adjacement((j, i), non_zero_list, \
                                                  HEIGHT, WIDTH)
                        if len(adj_set & edge_groups[key]) > 0:
                            is_contain = True
                            edge_groups[key].add((j, i))
                            break

                    if not is_contain:
                        edge_groups.update({count: {(j, i)}})
                        count += 1 
    return edge_groups
                


In [73]:
re_img = rescale_img(img, 10)
_, mag = get_img_gradient_info(re_img)
raw_nonzero = np.nonzero(mag)
non_zero_list = list(zip(raw_nonzero[0], raw_nonzero[1]))
mag.shape

(296, 144)

In [ ]:
non_zero_list.sort(key=lambda tup: tup[1])
for i in non_zero_list:
    print(i)

(1, 0)
(2, 0)
(3, 0)
(4, 0)
(5, 0)
(8, 0)
(9, 0)
(10, 0)
(31, 0)
(32, 0)
(45, 0)
(46, 0)
(47, 0)
(48, 0)
(49, 0)
(50, 0)
(51, 0)
(52, 0)
(53, 0)
(54, 0)
(55, 0)
(56, 0)
(57, 0)
(58, 0)
(59, 0)
(60, 0)
(101, 0)
(102, 0)
(103, 0)
(104, 0)
(105, 0)
(106, 0)
(107, 0)
(108, 0)
(109, 0)
(118, 0)
(119, 0)
(120, 0)
(121, 0)
(122, 0)
(223, 0)
(224, 0)
(225, 0)
(226, 0)
(227, 0)
(247, 0)
(248, 0)
(249, 0)
(250, 0)
(251, 0)
(252, 0)
(289, 0)
(290, 0)
(0, 1)
(1, 1)
(2, 1)
(3, 1)
(4, 1)
(5, 1)
(8, 1)
(9, 1)
(10, 1)
(31, 1)
(32, 1)
(45, 1)
(46, 1)
(47, 1)
(48, 1)
(49, 1)
(50, 1)
(51, 1)
(52, 1)
(53, 1)
(54, 1)
(55, 1)
(56, 1)
(57, 1)
(58, 1)
(59, 1)
(60, 1)
(61, 1)
(62, 1)
(63, 1)
(64, 1)
(65, 1)
(66, 1)
(67, 1)
(68, 1)
(69, 1)
(70, 1)
(71, 1)
(72, 1)
(73, 1)
(74, 1)
(75, 1)
(76, 1)
(77, 1)
(78, 1)
(79, 1)
(80, 1)
(81, 1)
(82, 1)
(83, 1)
(84, 1)
(85, 1)
(86, 1)
(87, 1)
(88, 1)
(89, 1)
(90, 1)
(91, 1)
(92, 1)
(93, 1)
(94, 1)
(95, 1)
(96, 1)
(97, 1)
(98, 1)
(99, 1)
(100, 1)
(101, 1)
(102, 1)
(103, 1)


(202, 12)
(203, 12)
(204, 12)
(205, 12)
(206, 12)
(207, 12)
(208, 12)
(209, 12)
(210, 12)
(211, 12)
(214, 12)
(215, 12)
(216, 12)
(217, 12)
(223, 12)
(224, 12)
(225, 12)
(226, 12)
(227, 12)
(230, 12)
(231, 12)
(232, 12)
(233, 12)
(234, 12)
(235, 12)
(236, 12)
(237, 12)
(238, 12)
(239, 12)
(240, 12)
(241, 12)
(242, 12)
(243, 12)
(244, 12)
(247, 12)
(248, 12)
(249, 12)
(250, 12)
(251, 12)
(252, 12)
(257, 12)
(258, 12)
(259, 12)
(260, 12)
(261, 12)
(262, 12)
(280, 12)
(281, 12)
(282, 12)
(283, 12)
(284, 12)
(285, 12)
(286, 12)
(287, 12)
(288, 12)
(289, 12)
(290, 12)
(1, 13)
(2, 13)
(3, 13)
(4, 13)
(5, 13)
(6, 13)
(7, 13)
(8, 13)
(9, 13)
(10, 13)
(17, 13)
(18, 13)
(19, 13)
(20, 13)
(21, 13)
(22, 13)
(23, 13)
(24, 13)
(25, 13)
(26, 13)
(31, 13)
(32, 13)
(36, 13)
(37, 13)
(38, 13)
(39, 13)
(40, 13)
(41, 13)
(42, 13)
(43, 13)
(44, 13)
(45, 13)
(46, 13)
(47, 13)
(48, 13)
(49, 13)
(50, 13)
(51, 13)
(56, 13)
(57, 13)
(58, 13)
(59, 13)
(60, 13)
(61, 13)
(62, 13)
(118, 13)
(119, 13)
(120, 13)
(121

(157, 21)
(158, 21)
(159, 21)
(160, 21)
(161, 21)
(162, 21)
(163, 21)
(165, 21)
(166, 21)
(168, 21)
(172, 21)
(173, 21)
(174, 21)
(175, 21)
(176, 21)
(177, 21)
(178, 21)
(179, 21)
(180, 21)
(181, 21)
(182, 21)
(183, 21)
(184, 21)
(187, 21)
(188, 21)
(189, 21)
(190, 21)
(192, 21)
(193, 21)
(194, 21)
(195, 21)
(196, 21)
(199, 21)
(200, 21)
(201, 21)
(202, 21)
(203, 21)
(204, 21)
(205, 21)
(206, 21)
(207, 21)
(208, 21)
(209, 21)
(210, 21)
(211, 21)
(215, 21)
(217, 21)
(223, 21)
(224, 21)
(225, 21)
(226, 21)
(227, 21)
(230, 21)
(231, 21)
(232, 21)
(233, 21)
(234, 21)
(235, 21)
(236, 21)
(237, 21)
(238, 21)
(239, 21)
(240, 21)
(241, 21)
(242, 21)
(243, 21)
(244, 21)
(247, 21)
(248, 21)
(249, 21)
(250, 21)
(251, 21)
(252, 21)
(257, 21)
(258, 21)
(259, 21)
(260, 21)
(261, 21)
(262, 21)
(263, 21)
(280, 21)
(281, 21)
(282, 21)
(283, 21)
(284, 21)
(285, 21)
(286, 21)
(287, 21)
(288, 21)
(289, 21)
(290, 21)
(291, 21)
(292, 21)
(293, 21)
(294, 21)
(0, 22)
(1, 22)
(2, 22)
(3, 22)
(4, 22)
(5, 22)
(6

(38, 30)
(39, 30)
(40, 30)
(41, 30)
(46, 30)
(47, 30)
(48, 30)
(49, 30)
(50, 30)
(51, 30)
(56, 30)
(57, 30)
(58, 30)
(59, 30)
(60, 30)
(61, 30)
(62, 30)
(63, 30)
(64, 30)
(72, 30)
(73, 30)
(74, 30)
(75, 30)
(76, 30)
(77, 30)
(78, 30)
(79, 30)
(80, 30)
(82, 30)
(83, 30)
(84, 30)
(85, 30)
(86, 30)
(87, 30)
(93, 30)
(94, 30)
(95, 30)
(96, 30)
(97, 30)
(98, 30)
(99, 30)
(100, 30)
(101, 30)
(102, 30)
(103, 30)
(104, 30)
(106, 30)
(107, 30)
(108, 30)
(109, 30)
(110, 30)
(111, 30)
(118, 30)
(119, 30)
(120, 30)
(121, 30)
(122, 30)
(128, 30)
(129, 30)
(130, 30)
(131, 30)
(132, 30)
(133, 30)
(134, 30)
(163, 30)
(165, 30)
(190, 30)
(192, 30)
(223, 30)
(224, 30)
(225, 30)
(226, 30)
(227, 30)
(230, 30)
(231, 30)
(232, 30)
(233, 30)
(234, 30)
(235, 30)
(236, 30)
(237, 30)
(238, 30)
(239, 30)
(240, 30)
(241, 30)
(242, 30)
(243, 30)
(244, 30)
(247, 30)
(248, 30)
(249, 30)
(250, 30)
(251, 30)
(252, 30)
(280, 30)
(281, 30)
(282, 30)
(283, 30)
(284, 30)
(285, 30)
(286, 30)
(287, 30)
(288, 30)
(289, 30)
(

(36, 41)
(37, 41)
(38, 41)
(39, 41)
(40, 41)
(41, 41)
(42, 41)
(43, 41)
(46, 41)
(47, 41)
(48, 41)
(49, 41)
(50, 41)
(51, 41)
(56, 41)
(57, 41)
(58, 41)
(59, 41)
(60, 41)
(61, 41)
(62, 41)
(63, 41)
(64, 41)
(118, 41)
(119, 41)
(120, 41)
(121, 41)
(122, 41)
(127, 41)
(128, 41)
(129, 41)
(130, 41)
(131, 41)
(132, 41)
(133, 41)
(134, 41)
(135, 41)
(144, 41)
(145, 41)
(146, 41)
(147, 41)
(148, 41)
(149, 41)
(151, 41)
(152, 41)
(153, 41)
(154, 41)
(155, 41)
(156, 41)
(157, 41)
(163, 41)
(165, 41)
(172, 41)
(173, 41)
(174, 41)
(175, 41)
(176, 41)
(179, 41)
(180, 41)
(181, 41)
(182, 41)
(183, 41)
(184, 41)
(190, 41)
(192, 41)
(199, 41)
(200, 41)
(201, 41)
(202, 41)
(203, 41)
(206, 41)
(207, 41)
(208, 41)
(209, 41)
(210, 41)
(211, 41)
(212, 41)
(223, 41)
(224, 41)
(225, 41)
(226, 41)
(227, 41)
(230, 41)
(231, 41)
(232, 41)
(233, 41)
(234, 41)
(235, 41)
(236, 41)
(237, 41)
(238, 41)
(239, 41)
(240, 41)
(241, 41)
(242, 41)
(243, 41)
(244, 41)
(247, 41)
(248, 41)
(249, 41)
(250, 41)
(251, 41)
(25

(23, 53)
(26, 53)
(27, 53)
(28, 53)
(31, 53)
(32, 53)
(46, 53)
(47, 53)
(48, 53)
(49, 53)
(50, 53)
(51, 53)
(56, 53)
(57, 53)
(58, 53)
(59, 53)
(60, 53)
(61, 53)
(62, 53)
(63, 53)
(64, 53)
(118, 53)
(119, 53)
(120, 53)
(121, 53)
(122, 53)
(151, 53)
(152, 53)
(153, 53)
(154, 53)
(155, 53)
(156, 53)
(157, 53)
(158, 53)
(163, 53)
(165, 53)
(171, 53)
(172, 53)
(173, 53)
(174, 53)
(175, 53)
(176, 53)
(177, 53)
(178, 53)
(179, 53)
(180, 53)
(181, 53)
(182, 53)
(183, 53)
(184, 53)
(185, 53)
(190, 53)
(192, 53)
(206, 53)
(207, 53)
(208, 53)
(209, 53)
(210, 53)
(223, 53)
(224, 53)
(225, 53)
(226, 53)
(227, 53)
(230, 53)
(231, 53)
(232, 53)
(233, 53)
(234, 53)
(235, 53)
(236, 53)
(237, 53)
(238, 53)
(239, 53)
(240, 53)
(241, 53)
(242, 53)
(243, 53)
(244, 53)
(247, 53)
(248, 53)
(249, 53)
(250, 53)
(251, 53)
(252, 53)
(276, 53)
(277, 53)
(278, 53)
(279, 53)
(280, 53)
(281, 53)
(283, 53)
(284, 53)
(285, 53)
(286, 53)
(287, 53)
(288, 53)
(289, 53)
(290, 53)
(0, 54)
(1, 54)
(2, 54)
(3, 54)
(4, 54)
(

(110, 66)
(111, 66)
(118, 66)
(119, 66)
(120, 66)
(121, 66)
(122, 66)
(163, 66)
(165, 66)
(179, 66)
(180, 66)
(181, 66)
(182, 66)
(183, 66)
(184, 66)
(185, 66)
(190, 66)
(192, 66)
(223, 66)
(224, 66)
(225, 66)
(226, 66)
(227, 66)
(230, 66)
(231, 66)
(232, 66)
(233, 66)
(234, 66)
(235, 66)
(236, 66)
(237, 66)
(238, 66)
(239, 66)
(240, 66)
(241, 66)
(242, 66)
(243, 66)
(244, 66)
(247, 66)
(248, 66)
(249, 66)
(250, 66)
(251, 66)
(252, 66)
(276, 66)
(277, 66)
(278, 66)
(279, 66)
(280, 66)
(281, 66)
(283, 66)
(284, 66)
(285, 66)
(286, 66)
(287, 66)
(288, 66)
(289, 66)
(290, 66)
(291, 66)
(292, 66)
(293, 66)
(294, 66)
(0, 67)
(1, 67)
(2, 67)
(3, 67)
(4, 67)
(5, 67)
(8, 67)
(9, 67)
(10, 67)
(13, 67)
(14, 67)
(15, 67)
(18, 67)
(19, 67)
(20, 67)
(21, 67)
(22, 67)
(23, 67)
(26, 67)
(27, 67)
(28, 67)
(31, 67)
(32, 67)
(34, 67)
(35, 67)
(36, 67)
(37, 67)
(38, 67)
(46, 67)
(47, 67)
(48, 67)
(49, 67)
(50, 67)
(51, 67)
(69, 67)
(70, 67)
(71, 67)
(72, 67)
(73, 67)
(74, 67)
(75, 67)
(76, 67)
(77, 67)
(

In [75]:
edgegroups = get_edgegroups_v2(mag, non_zero_list,296,144)
edgegroups

[DEBUG] WIDTH:0 HEIGHT:0
[DEBUG] WIDTH:0 HEIGHT:1
[DEBUG] WIDTH:0 HEIGHT:2
[DEBUG] KEY_LIST:  [0]
[DEBUG] WIDTH:0 HEIGHT:3
[DEBUG] KEY_LIST:  [0]
[DEBUG] WIDTH:0 HEIGHT:4
[DEBUG] KEY_LIST:  [0]
[DEBUG] WIDTH:0 HEIGHT:5
[DEBUG] KEY_LIST:  [0]
[DEBUG] WIDTH:0 HEIGHT:6
[DEBUG] WIDTH:0 HEIGHT:7
[DEBUG] WIDTH:0 HEIGHT:8
[DEBUG] KEY_LIST:  [0]
[DEBUG] WIDTH:0 HEIGHT:9
[DEBUG] KEY_LIST:  [0, 1]
[DEBUG] WIDTH:0 HEIGHT:10
[DEBUG] KEY_LIST:  [0, 1]
[DEBUG] WIDTH:0 HEIGHT:11
[DEBUG] WIDTH:0 HEIGHT:12
[DEBUG] WIDTH:0 HEIGHT:13
[DEBUG] WIDTH:0 HEIGHT:14
[DEBUG] WIDTH:0 HEIGHT:15
[DEBUG] WIDTH:0 HEIGHT:16
[DEBUG] WIDTH:0 HEIGHT:17
[DEBUG] WIDTH:0 HEIGHT:18
[DEBUG] WIDTH:0 HEIGHT:19
[DEBUG] WIDTH:0 HEIGHT:20
[DEBUG] WIDTH:0 HEIGHT:21
[DEBUG] WIDTH:0 HEIGHT:22
[DEBUG] WIDTH:0 HEIGHT:23
[DEBUG] WIDTH:0 HEIGHT:24
[DEBUG] WIDTH:0 HEIGHT:25
[DEBUG] WIDTH:0 HEIGHT:26
[DEBUG] WIDTH:0 HEIGHT:27
[DEBUG] WIDTH:0 HEIGHT:28
[DEBUG] WIDTH:0 HEIGHT:29
[DEBUG] WIDTH:0 HEIGHT:30
[DEBUG] WIDTH:0 HEIGHT:31
[DEBUG] KEY

[DEBUG] WIDTH:0 HEIGHT:250
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7]
[DEBUG] WIDTH:0 HEIGHT:251
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7]
[DEBUG] WIDTH:0 HEIGHT:252
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7]
[DEBUG] WIDTH:0 HEIGHT:253
[DEBUG] WIDTH:0 HEIGHT:254
[DEBUG] WIDTH:0 HEIGHT:255
[DEBUG] WIDTH:0 HEIGHT:256
[DEBUG] WIDTH:0 HEIGHT:257
[DEBUG] WIDTH:0 HEIGHT:258
[DEBUG] WIDTH:0 HEIGHT:259
[DEBUG] WIDTH:0 HEIGHT:260
[DEBUG] WIDTH:0 HEIGHT:261
[DEBUG] WIDTH:0 HEIGHT:262
[DEBUG] WIDTH:0 HEIGHT:263
[DEBUG] WIDTH:0 HEIGHT:264
[DEBUG] WIDTH:0 HEIGHT:265
[DEBUG] WIDTH:0 HEIGHT:266
[DEBUG] WIDTH:0 HEIGHT:267
[DEBUG] WIDTH:0 HEIGHT:268
[DEBUG] WIDTH:0 HEIGHT:269
[DEBUG] WIDTH:0 HEIGHT:270
[DEBUG] WIDTH:0 HEIGHT:271
[DEBUG] WIDTH:0 HEIGHT:272
[DEBUG] WIDTH:0 HEIGHT:273
[DEBUG] WIDTH:0 HEIGHT:274
[DEBUG] WIDTH:0 HEIGHT:275
[DEBUG] WIDTH:0 HEIGHT:276
[DEBUG] WIDTH:0 HEIGHT:277
[DEBUG] WIDTH:0 HEIGHT:278
[DEBUG] WIDTH:0 HEIGHT:279
[DEBUG] WIDTH:0 HEIGHT:280
[DEBUG] WIDTH:0 HEIGHT:281
[DEB

[DEBUG] WIDTH:1 HEIGHT:121
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8]
[DEBUG] WIDTH:1 HEIGHT:122
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8]
[DEBUG] WIDTH:1 HEIGHT:123
[DEBUG] WIDTH:1 HEIGHT:124
[DEBUG] WIDTH:1 HEIGHT:125
[DEBUG] WIDTH:1 HEIGHT:126
[DEBUG] WIDTH:1 HEIGHT:127
[DEBUG] WIDTH:1 HEIGHT:128
[DEBUG] WIDTH:1 HEIGHT:129
[DEBUG] WIDTH:1 HEIGHT:130
[DEBUG] WIDTH:1 HEIGHT:131
[DEBUG] WIDTH:1 HEIGHT:132
[DEBUG] WIDTH:1 HEIGHT:133
[DEBUG] WIDTH:1 HEIGHT:134
[DEBUG] WIDTH:1 HEIGHT:135
[DEBUG] WIDTH:1 HEIGHT:136
[DEBUG] WIDTH:1 HEIGHT:137
[DEBUG] WIDTH:1 HEIGHT:138
[DEBUG] WIDTH:1 HEIGHT:139
[DEBUG] WIDTH:1 HEIGHT:140
[DEBUG] WIDTH:1 HEIGHT:141
[DEBUG] WIDTH:1 HEIGHT:142
[DEBUG] WIDTH:1 HEIGHT:143
[DEBUG] WIDTH:1 HEIGHT:144
[DEBUG] WIDTH:1 HEIGHT:145
[DEBUG] WIDTH:1 HEIGHT:146
[DEBUG] WIDTH:1 HEIGHT:147
[DEBUG] WIDTH:1 HEIGHT:148
[DEBUG] WIDTH:1 HEIGHT:149
[DEBUG] WIDTH:1 HEIGHT:150
[DEBUG] WIDTH:1 HEIGHT:151
[DEBUG] WIDTH:1 HEIGHT:152
[DEBUG] WIDTH:1 HEIGHT:153
[DEBUG] WIDTH:1

[DEBUG] WIDTH:2 HEIGHT:56
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
[DEBUG] WIDTH:2 HEIGHT:57
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
[DEBUG] WIDTH:2 HEIGHT:58
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
[DEBUG] WIDTH:2 HEIGHT:59
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
[DEBUG] WIDTH:2 HEIGHT:60
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
[DEBUG] WIDTH:2 HEIGHT:61
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
[DEBUG] WIDTH:2 HEIGHT:62
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
[DEBUG] WIDTH:2 HEIGHT:63
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
[DEBUG] WIDTH:2 HEIGHT:64
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
[DEBUG] WIDTH:2 HEIGHT:65
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
[DEBUG] WIDTH:2 HEIGHT:66
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
[DEBUG] WIDTH:2 HEIGHT:67
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
[DEBUG] WIDTH:2 HEIGHT:68
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
[DEBUG] WIDT

[DEBUG] WIDTH:2 HEIGHT:248
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
[DEBUG] WIDTH:2 HEIGHT:249
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
[DEBUG] WIDTH:2 HEIGHT:250
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
[DEBUG] WIDTH:2 HEIGHT:251
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
[DEBUG] WIDTH:2 HEIGHT:252
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
[DEBUG] WIDTH:2 HEIGHT:253
[DEBUG] WIDTH:2 HEIGHT:254
[DEBUG] WIDTH:2 HEIGHT:255
[DEBUG] WIDTH:2 HEIGHT:256
[DEBUG] WIDTH:2 HEIGHT:257
[DEBUG] WIDTH:2 HEIGHT:258
[DEBUG] WIDTH:2 HEIGHT:259
[DEBUG] WIDTH:2 HEIGHT:260
[DEBUG] WIDTH:2 HEIGHT:261
[DEBUG] WIDTH:2 HEIGHT:262
[DEBUG] WIDTH:2 HEIGHT:263
[DEBUG] WIDTH:2 HEIGHT:264
[DEBUG] WIDTH:2 HEIGHT:265
[DEBUG] WIDTH:2 HEIGHT:266
[DEBUG] WIDTH:2 HEIGHT:267
[DEBUG] WIDTH:2 HEIGHT:268
[DEBUG] WIDTH:2 HEIGHT:269
[DEBUG] WIDTH:2 HEIGHT:270
[DEBUG] WIDTH:2 HEIGHT:271
[DEBUG] WIDTH:2 HEIGHT:272
[DEBUG] WIDTH:2 HEIGHT:273
[DEBUG] WIDTH:2 HEIGHT:274
[DEBUG] WIDTH:2 HEIGH

...

[DEBUG] WIDTH:142 HEIGHT:123
[DEBUG] WIDTH:142 HEIGHT:124
[DEBUG] WIDTH:142 HEIGHT:125
[DEBUG] WIDTH:142 HEIGHT:126
[DEBUG] WIDTH:142 HEIGHT:127
[DEBUG] WIDTH:142 HEIGHT:128
[DEBUG] WIDTH:142 HEIGHT:129
[DEBUG] WIDTH:142 HEIGHT:130
[DEBUG] WIDTH:142 HEIGHT:131
[DEBUG] WIDTH:142 HEIGHT:132
[DEBUG] WIDTH:142 HEIGHT:133
[DEBUG] WIDTH:142 HEIGHT:134
[DEBUG] WIDTH:142 HEIGHT:135
[DEBUG] WIDTH:142 HEIGHT:136
[DEBUG] WIDTH:142 HEIGHT:137
[DEBUG] WIDTH:142 HEIGHT:138
[DEBUG] WIDTH:142 HEIGHT:139
[DEBUG] WIDTH:142 HEIGHT:140
[DEBUG] WIDTH:142 HEIGHT:141
[DEBUG] WIDTH:142 HEIGHT:142
[DEBUG] WIDTH:142 HEIGHT:143
[DEBUG] WIDTH:142 HEIGHT:144
[DEBUG] WIDTH:142 HEIGHT:145
[DEBUG] WIDTH:142 HEIGHT:146
[DEBUG] WIDTH:142 HEIGHT:147
[DEBUG] WIDTH:142 HEIGHT:148
[DEBUG] WIDTH:142 HEIGHT:149
[DEBUG] WIDTH:142 HEIGHT:150
[DEBUG] WIDTH:142 HEIGHT:151
[DEBUG] WIDTH:142 HEIGHT:152
[DEBUG] WIDTH:142 HEIGHT:153
[DEBUG] WIDTH:142 HEIGHT:154
[DEBUG] WIDTH:142 HEIGHT:155
[DEBUG] WIDTH:142 HEIGHT:156
[DEBUG] WIDTH:

[DEBUG] WIDTH:142 HEIGHT:290
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75]
[DEBUG] WIDTH:142 HEIGHT:291
[DEBUG] WIDTH:142 HEIGHT:292
[DEBUG] WIDTH:142 HEIGHT:293
[DEBUG] WIDTH:142 HEIGHT:294
[DEBUG] WIDTH:142 HEIGHT:295
[DEBUG] WIDTH:143 HEIGHT:0
[DEBUG] WIDTH:143 HEIGHT:1
[DEBUG] WIDTH:143 HEIGHT:2
[DEBUG] WIDTH:143 HEIGHT:3
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75]
[DEBUG] WIDTH:143 HEIGHT:4
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 1

[DEBUG] WIDTH:143 HEIGHT:119
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75]
[DEBUG] WIDTH:143 HEIGHT:120
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75]
[DEBUG] WIDTH:143 HEIGHT:121
[DEBUG] KEY_LIST:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68,

[DEBUG] WIDTH:143 HEIGHT:253
[DEBUG] WIDTH:143 HEIGHT:254
[DEBUG] WIDTH:143 HEIGHT:255
[DEBUG] WIDTH:143 HEIGHT:256
[DEBUG] WIDTH:143 HEIGHT:257
[DEBUG] WIDTH:143 HEIGHT:258
[DEBUG] WIDTH:143 HEIGHT:259
[DEBUG] WIDTH:143 HEIGHT:260
[DEBUG] WIDTH:143 HEIGHT:261
[DEBUG] WIDTH:143 HEIGHT:262
[DEBUG] WIDTH:143 HEIGHT:263
[DEBUG] WIDTH:143 HEIGHT:264
[DEBUG] WIDTH:143 HEIGHT:265
[DEBUG] WIDTH:143 HEIGHT:266
[DEBUG] WIDTH:143 HEIGHT:267
[DEBUG] WIDTH:143 HEIGHT:268
[DEBUG] WIDTH:143 HEIGHT:269
[DEBUG] WIDTH:143 HEIGHT:270
[DEBUG] WIDTH:143 HEIGHT:271
[DEBUG] WIDTH:143 HEIGHT:272
[DEBUG] WIDTH:143 HEIGHT:273
[DEBUG] WIDTH:143 HEIGHT:274
[DEBUG] WIDTH:143 HEIGHT:275
[DEBUG] WIDTH:143 HEIGHT:276
[DEBUG] WIDTH:143 HEIGHT:277
[DEBUG] WIDTH:143 HEIGHT:278
[DEBUG] WIDTH:143 HEIGHT:279
[DEBUG] WIDTH:143 HEIGHT:280
[DEBUG] WIDTH:143 HEIGHT:281
[DEBUG] WIDTH:143 HEIGHT:282
[DEBUG] WIDTH:143 HEIGHT:283
[DEBUG] WIDTH:143 HEIGHT:284
[DEBUG] WIDTH:143 HEIGHT:285
[DEBUG] WIDTH:143 HEIGHT:286
[DEBUG] WIDTH:

{0: {(4, 36),
  (8, 63),
  (7, 25),
  (1, 64),
  (2, 78),
  (8, 142),
  (5, 84),
  (6, 98),
  (10, 97),
  (0, 55),
  (3, 2),
  (8, 87),
  (1, 40),
  (4, 35),
  (8, 38),
  (7, 22),
  (1, 89),
  (2, 73),
  (5, 93),
  (6, 101),
  (10, 104),
  (3, 11),
  (8, 94),
  (1, 33),
  (4, 42),
  (8, 45),
  (7, 15),
  (1, 82),
  (2, 64),
  (5, 53),
  (9, 50),
  (10, 128),
  (5, 70),
  (6, 92),
  (10, 19),
  (0, 5),
  (1, 137),
  (3, 112),
  (8, 69),
  (3, 129),
  (4, 17),
  (2, 91),
  (5, 62),
  (9, 59),
  (10, 139),
  (0, 109),
  (5, 79),
  (6, 87),
  (10, 26),
  (0, 28),
  (1, 130),
  (3, 121),
  (8, 76),
  (0, 139),
  (1, 51),
  (3, 134),
  (4, 24),
  (7, 125),
  (2, 82),
  (5, 39),
  (9, 60),
  (5, 72),
  (0, 19),
  (3, 126),
  (4, 112),
  (8, 115),
  (0, 130),
  (1, 52),
  (3, 143),
  (4, 7),
  (7, 122),
  (2, 45),
  (5, 32),
  (9, 37),
  (0, 123),
  (10, 12),
  (3, 103),
  (4, 127),
  (8, 122),
  (1, 13),
  (4, 14),
  (7, 115),
  (5, 41),
  (9, 46),
  (7, 128),
  (0, 114),
  (10, 55),
  (3, 10

In [86]:
for key in edgegroups.keys():
    group_list = list(edgegroups[key])
    smallest_x = group_list[0][0]
    biggest_x = group_list[-1][0]
    smallest_y = group_list[0][1]
    biggest_y = 0
    for i in group_list:
        if biggest_y <i[1]:
            biggest_y = i[1]
    cv2.rectangle(re_img, (smallest_y, biggest_x),  (biggest_y, smallest_x), (255, 0, 0), 3)

show_img(re_img)